#Week 4 Assignment
##Introduction/Business Problem

This report will examine the optimal site for an law office in Union or Essex Counties, New Jersey.  These counties were chosen as counties with a similar combination of urban and dense suburban municipalities.  The working assumption is a law office will be most successful where the neighborhood is similar to other neighborhoods with a successful bar, but where there is less competition.  There are two county seats in the area being reviewed, Newark and Elizabeth.  Because the Superior Court for each county is located in the county seat, there are generally a higher concentration of law near those sites, so we need to examing whether to adjust for that effect. Newark and Elizabeth both have multiple zip codes/neighborhoods, so we will need to identify the neighborhoods nearest the courthouse.

To do this analysis, we will retrieve location data for all zip codes in the two counties, examine FourSquare data for nearby shops and services, then look for neighborhoods that are similar to other neighborhoods in those counties that have a higher incidence than average of Lawyer venues, but themselves have a low incidence of Lawyer venues.  

#Week 4 Assignment 
##Data

This analysis used ZipExpress to retrieve zip codes by county. 

In [2]:
import pandas as pd 
union = pd.read_html("https://www.getzips.com/cgi-bin/ziplook.exe?What=3&County=union&State=NJ&Submit=Look+It+Up")[2]
essex = pd.read_html("https://www.getzips.com/cgi-bin/ziplook.exe?What=3&County=Essex&State=NJ&Submit=Look+It+Up")[2]
union=union.drop(0)
essex=essex.drop(0)
display(union.head())
display(essex.head())

0              1      2    3
1  07088   Vauxhall, NJ  Union  908
2  07901     Summit, NJ  Union  908
3  07091  Westfield, NJ  Union  908
4  07083      Union, NJ  Union  908
5  07090  Westfield, NJ  Union  908

0           1      2    3
1  07104  Newark, NJ  Essex  973
2  07103  Newark, NJ  Essex  973
3  07107  Newark, NJ  Essex  973
4  07105  Newark, NJ  Essex  973
5  07106  Newark, NJ  Essex  973

The information for the two counties was then joined into a single dataframe.  Column names were added in the new dataframe. 

In [3]:
counties = union
counties=counties.append(essex)
counties.columns=['Zip','City','County','AreaCode']
counties

Zip                  City County AreaCode
1   07088          Vauxhall, NJ  Union      908
2   07901            Summit, NJ  Union      908
3   07091         Westfield, NJ  Union      908
4   07083             Union, NJ  Union      908
5   07090         Westfield, NJ  Union      908
6   07204      Roselle Park, NJ  Union      908
7   07203           Roselle, NJ  Union      908
8   07208         Elizabeth, NJ  Union      908
9   07206     Elizabethport, NJ  Union      908
10  07205          Hillside, NJ  Union      908
11  07207         Elizabeth, NJ  Union      908
12  07092      Mountainside, NJ  Union      908
13  07922  Berkeley Heights, NJ  Union      908
14  07902            Summit, NJ  Union      908
15  07202         Elizabeth, NJ  Union      908
16  07974    New Providence, NJ  Union      908
17  07201         Elizabeth, NJ  Union      908
18  07027           Garwood, NJ  Union      908
19  07062        Plainfield, NJ  Union      908
20  07033        Kenilworth, NJ  Union      908
21  07061        Plainfield, NJ  Union      908
22  07023           Fanwood, NJ  Union      908
23  07076     Scotch Plains, NJ  Union      908
24  07081       Springfield, NJ  Union      973
25  07066             Clark, NJ  Union      908
26  07063        Plainfield, NJ  Union      908
27  07065            Rahway, NJ  Union      732
28  07016          Cranford, NJ  Union      908
29  07060        Plainfield, NJ  Union      908
30  07036            Linden, NJ  Union      908
..    ...                   ...    ...      ...
16  07184            Newark, NJ  Essex      973
17  07175            Newark, NJ  Essex      973
18  07199            Newark, NJ  Essex      973
19  07192            Newark, NJ  Essex      973
20  07191            Newark, NJ  Essex      973
21  07189            Newark, NJ  Essex      973
22  07114            Newark, NJ  Essex      973
23  07110            Nutley, NJ  Essex      973
24  07109        Belleville, NJ  Essex      973
25  07108            Newark, NJ  Essex      973
26  07111         Irvington, NJ  Essex      973
27  07193            Newark, NJ  Essex      973
28  07112            Newark, NJ  Essex      973
29  07195            Newark, NJ  Essex      973
30  07044            Verona, NJ  Essex      973
31  07019       East Orange, NJ  Essex      973
32  07018       East Orange, NJ  Essex      973
33  07021       Essex Fells, NJ  Essex      973
34  07039        Livingston, NJ  Essex      973
35  07028        Glen Ridge, NJ  Essex      973
36  07017       East Orange, NJ  Essex      973
37  07004         Fairfield, NJ  Essex      973
38  07003        Bloomfield, NJ  Essex      973
39  07006          Caldwell, NJ  Essex      973
40  07009       Cedar Grove, NJ  Essex      973
41  07007          Caldwell, NJ  Essex      973
42  07041          Millburn, NJ  Essex      973
43  07040         Maplewood, NJ  Essex      973
44  07043         Montclair, NJ  Essex      973
45  07042         Montclair, NJ  Essex      973

[75 rows x 4 columns]

I obtained longitude and latitude information by postal code from http://download.geonames.org (http://download.geonames.org/export/zip/US.zip), and read them into a dataframe. 

In [4]:
# The code was removed by Watson Studio for sharing.

Country            PlaceName   State                  County  Latitude  \
Code                                                                           
99553      US               Akutan  Alaska          Aleutians East   54.1430   
99571      US             Cold Bay  Alaska          Aleutians East   55.1858   
99583      US           False Pass  Alaska          Aleutians East   54.8542   
99612      US            King Cove  Alaska          Aleutians East   55.0628   
99661      US           Sand Point  Alaska          Aleutians East   55.3192   
99546      US                 Adak  Alaska     Aleutians West (CA)   51.8740   
99547      US                 Atka  Alaska     Aleutians West (CA)   52.1961   
99591      US  Saint George Island  Alaska     Aleutians West (CA)   56.5944   
99638      US             Nikolski  Alaska     Aleutians West (CA)   52.9381   
99660      US    Saint Paul Island  Alaska     Aleutians West (CA)   57.1842   
99685      US             Unalaska  Alaska     Aleutians West (CA)   53.8871   
99692      US         Dutch Harbor  Alaska     Aleutians West (CA)   53.8898   
99501      US            Anchorage  Alaska  Anchorage Municipality   61.2116   
99502      US            Anchorage  Alaska  Anchorage Municipality   61.1661   
99503      US            Anchorage  Alaska  Anchorage Municipality   61.1900   
99504      US            Anchorage  Alaska  Anchorage Municipality   61.2037   
99505      US                 Jber  Alaska  Anchorage Municipality   59.8666   
99506      US                 Jber  Alaska  Anchorage Municipality   59.8666   
99507      US            Anchorage  Alaska  Anchorage Municipality   61.1535   
99508      US            Anchorage  Alaska  Anchorage Municipality   61.2060   
99509      US            Anchorage  Alaska  Anchorage Municipality   61.2181   
99510      US            Anchorage  Alaska  Anchorage Municipality   61.1446   
99511      US            Anchorage  Alaska  Anchorage Municipality   61.0683   
99513      US            Anchorage  Alaska  Anchorage Municipality   61.2149   
99514      US            Anchorage  Alaska  Anchorage Municipality   61.2181   
99515      US            Anchorage  Alaska  Anchorage Municipality   61.1194   
99516      US            Anchorage  Alaska  Anchorage Municipality   61.1054   
99517      US            Anchorage  Alaska  Anchorage Municipality   61.1901   
99518      US            Anchorage  Alaska  Anchorage Municipality   61.1549   
99519      US            Anchorage  Alaska  Anchorage Municipality   61.1089   
...       ...                  ...     ...                     ...       ...   
96512      US               APO AA     NaN                     NaN   52.7242   
96513      US               APO AA     NaN                     NaN   58.6883   
96514      US               FPO AA     NaN                     NaN   28.2280   
96516      US               FPO AA     NaN                     NaN   28.2280   
96517      US               FPO AA     NaN                     NaN   34.2322   
96518      US               APO AA     NaN                     NaN   19.2811   
96520      US               APO AA     NaN                     NaN   -6.2146   
96521      US               FPO AA     NaN                     NaN   22.2783   
96522      US               FPO AA     NaN                     NaN   22.2783   
96531      US               FPO AA     NaN                     NaN  -43.5333   
96534      US               FPO AA     NaN                     NaN    1.2897   
96539      US               FPO AA     NaN                     NaN   13.4757   
96540      US               FPO AA     NaN                     NaN   13.4757   
96541      US               APO AA     NaN                     NaN   13.4757   
96542      US               APO AA     NaN                     NaN   13.4757   
96543      US               APO AA     NaN                     NaN   13.4757   
96546      US               APO AA     NaN                     NaN   13.7540   
96548 

The latitude and longitude were added to the combined dataframe of zip codes by doing a lookup by zip code. 

In [5]:
counties['Latitude'] = list(codes.loc[counties['Zip']]['Latitude'])
counties['Longitude'] = list(codes.loc[counties['Zip']]['Longitude'])
counties.head()


Zip           City County AreaCode  Latitude  Longitude
1  07088   Vauxhall, NJ  Union      908   40.7179   -74.2829
2  07901     Summit, NJ  Union      908   40.7149   -74.3642
3  07091  Westfield, NJ  Union      908   40.6657   -74.2997
4  07083      Union, NJ  Union      908   40.6952   -74.2677
5  07090  Westfield, NJ  Union      908   40.6479   -74.3451

The result is information for 75 localities by zip code.

In [6]:
counties.shape

(75, 6)

Installing libraries for further analysis. 

In [12]:

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes --debug # uncomment this line if you haven't completed the Foursquare API lab
#from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes --debug # uncomment this line if you haven't completed the Foursquare API lab
#import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [13]:
CLIENT_ID = 'NVKUL15USCVWRI4MZGCL2XY2UZBVYF12D2BSBYENLELS2XQM' # your Foursquare ID
CLIENT_SECRET = '5W11RYKY003KS3RAGXU5JJ004R0D2QRRUONEMEHJIE1XAS5Y' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

#print('Your credentials:')
#print('CLIENT_ID: ' + CLIENT_ID)
#print('CLIENT_SECRET:' + CLIENT_SECRET)

Adding code to look up shops and services near the center of the zip code area. 

In [20]:
CATEGORY = '4d4b7105d754a06378d81259' # Shop & Service
#CATEGORY = '52f2ab2ebcbc57f1066b8b3f' #lawyer
radius = 3000
LIMIT = 300

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
#        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
#         url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&intent=browse&categoryId={}&client_secret={}&v={}&ll={},{}&limit={}'.format(            
            CLIENT_ID, 
            CATEGORY,
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        display(results)
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Retrieving data specifically for shops and services, category ID 4d4b7105d754a06378d81259, within 300 meters. We are retricting to the most relevant category because of the limit of 100 returned venues by latitude and longitude.   

In [26]:


nj_venues = getNearbyVenues(names=counties['City'] + " " + counties.Zip,
                                   latitudes=counties['Latitude'],
                                   longitudes=counties['Longitude'],
                                   radius=200
                                  )
nj_venues.head()

Vauxhall, NJ 07088


[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4a64ca9af964a520b2c61fe3',
   'name': 'Whole Foods Market',
   'location': {'address': '2245 Springfield Ave.',
    'crossStreet': 'Marion St',
    'lat': 40.7170552041893,
    'lng': -74.28654430825806,
    'labeledLatLngs': [{'label': 'display',
      'lat': 40.7170552041893,
      'lng': -74.28654430825806}],
    'distance': 321,
    'postalCode': '07088',
    'cc': 'US',
    'city': 'Vauxhall',
    'state': 'NJ',
    'country': 'United States',
    'formattedAddress': ['2245 Springfield Ave. (Marion St)',
     'Vauxhall, NJ 07088',
     'United States']},
   'categories': [{'id': '4bf58dd8d48988d118951735',
     'name': 'Grocery Store',
     'pluralName': 'Grocery Stores',
     'shortName': 'Grocery Store',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_grocery_',
      'suffix': '.png'},
 

Summit, NJ 07901


[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4c0ba0ad7e3fc928c884f582',
   'name': 'Summit Farmers Market',
   'location': {'address': 'DeForest Avenue & Beechwood',
    'crossStreet': 'Summit Bank parking lot',
    'lat': 40.71871051456713,
    'lng': -74.35879602084398,
    'labeledLatLngs': [{'label': 'display',
      'lat': 40.71871051456713,
      'lng': -74.35879602084398}],
    'distance': 622,
    'postalCode': '07901',
    'cc': 'US',
    'city': 'Summit',
    'state': 'NJ',
    'country': 'United States',
    'formattedAddress': ['DeForest Avenue & Beechwood (Summit Bank parking lot)',
     'Summit, NJ 07901',
     'United States']},
   'categories': [{'id': '4bf58dd8d48988d1fa941735',
     'name': 'Farmers Market',
     'pluralName': 'Farmers Markets',
     'shortName': "Farmer's Market",
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/sho

Westfield, NJ 07091


...

Montclair, NJ 07043


[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4b3a38e6f964a520836225e3',
   'name': "Angelbeck's Fine Wines, Spirits, and Beer",
   'location': {'address': '621 Valley Rd',
    'lat': 40.84200566758167,
    'lng': -74.20817146912617,
    'labeledLatLngs': [{'label': 'display',
      'lat': 40.84200566758167,
      'lng': -74.20817146912617}],
    'distance': 605,
    'postalCode': '07043',
    'cc': 'US',
    'city': 'Upper Montclair',
    'state': 'NJ',
    'country': 'United States',
    'formattedAddress': ['621 Valley Rd',
     'Upper Montclair, NJ 07043',
     'United States']},
   'categories': [{'id': '4bf58dd8d48988d119951735',
     'name': 'Wine Shop',
     'pluralName': 'Wine Shops',
     'shortName': 'Wine Shop',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_wineshop_',
      'suffix': '.png'},
     'primary': True}],
   'photo

Montclair, NJ 07042


[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4b845fe8f964a520a13131e3',
   'name': 'Amanti Vino',
   'location': {'address': '30 Church St',
    'lat': 40.81394812050306,
    'lng': -74.21893916100419,
    'labeledLatLngs': [{'label': 'display',
      'lat': 40.81394812050306,
      'lng': -74.21893916100419},
     {'label': 'entrance', 'lat': 40.813887, 'lng': -74.21907}],
    'distance': 226,
    'postalCode': '07042',
    'cc': 'US',
    'city': 'Montclair',
    'state': 'NJ',
    'country': 'United States',
    'formattedAddress': ['30 Church St',
     'Montclair, NJ 07042',
     'United States']},
   'categories': [{'id': '4bf58dd8d48988d119951735',
     'name': 'Wine Shop',
     'pluralName': 'Wine Shops',
     'shortName': 'Wine Shop',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/food_wineshop_',
      'suffix': '.png'},
     'primary

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Vauxhall, NJ 07088                40.7179                -74.2829   
1  Vauxhall, NJ 07088                40.7179                -74.2829   
2  Vauxhall, NJ 07088                40.7179                -74.2829   
3  Vauxhall, NJ 07088                40.7179                -74.2829   
4  Vauxhall, NJ 07088                40.7179                -74.2829   

                Venue  Venue Latitude  Venue Longitude Venue Category  
0  Whole Foods Market       40.717055       -74.286544  Grocery Store  
1         Wine Barrel       40.720694       -74.270667   Liquor Store  
2        Trader Joe's       40.722797       -74.295828  Grocery Store  
3            PetSmart       40.722963       -74.296005      Pet Store  
4              Target       40.715598       -74.284855  Big Box Store

Verifying that lawyer venues were received. 

In [28]:
print(nj_venues.shape)
nj_venues[nj_venues['Venue Category']=='Lawyer']

(7500, 7)


Neighborhood  Neighborhood Latitude  \
55            Vauxhall, NJ 07088                40.7179   
59            Vauxhall, NJ 07088                40.7179   
77            Vauxhall, NJ 07088                40.7179   
88            Vauxhall, NJ 07088                40.7179   
96            Vauxhall, NJ 07088                40.7179   
184             Summit, NJ 07901                40.7149   
195             Summit, NJ 07901                40.7149   
252          Westfield, NJ 07091                40.6657   
256          Westfield, NJ 07091                40.6657   
383              Union, NJ 07083                40.6952   
456          Westfield, NJ 07090                40.6479   
458          Westfield, NJ 07090                40.6479   
483          Westfield, NJ 07090                40.6479   
497          Westfield, NJ 07090                40.6479   
687            Roselle, NJ 07203                40.6530   
734          Elizabeth, NJ 07208                40.6747   
744          Elizabeth, NJ 07208                40.6747   
751          Elizabeth, NJ 07208                40.6747   
765          Elizabeth, NJ 07208                40.6747   
772          Elizabeth, NJ 07208                40.6747   
775          Elizabeth, NJ 07208                40.6747   
777          Elizabeth, NJ 07208                40.6747   
779          Elizabeth, NJ 07208                40.6747   
792          Elizabeth, NJ 07208                40.6747   
793          Elizabeth, NJ 07208                40.6747   
798          Elizabeth, NJ 07208                40.6747   
1056         Elizabeth, NJ 07207                40.6640   
1067         Elizabeth, NJ 07207                40.6640   
1068         Elizabeth, NJ 07207                40.6640   
1069         Elizabeth, NJ 07207                40.6640   
1073         Elizabeth, NJ 07207                40.6640   
1074         Elizabeth, NJ 07207                40.6640   
1083         Elizabeth, NJ 07207                40.6640   
1087         Elizabeth, NJ 07207                40.6640   
1153      Mountainside, NJ 07092                40.6785   
1185      Mountainside, NJ 07092                40.6785   
1287  Berkeley Heights, NJ 07922                40.6752   
1382            Summit, NJ 07902                40.7156   
1393            Summit, NJ 07902                40.7156   
1440         Elizabeth, NJ 07202                40.6565   
1445         Elizabeth, NJ 07202                40.6565   
1448         Elizabeth, NJ 07202                40.6565   
1456         Elizabeth, NJ 07202                40.6565   
1461         Elizabeth, NJ 07202                40.6565   
1470         Elizabeth, NJ 07202                40.6565   
1471         Elizabeth, NJ 07202                40.6565   
1481         Elizabeth, NJ 07202                40.6565   
1492         Elizabeth, NJ 07202                40.6565   
1495         Elizabeth, NJ 07202                40.6565   
1593    New Providence, NJ 07974                40.7004   
1597    New Providence, NJ 07974                40.7004   
1649         Elizabeth, NJ 07201                40.6717   
1661         Elizabeth, NJ 07201                40.6717   
1662         Elizabeth, NJ 07201                40.6717   
1673         Elizabeth, NJ 07201                40.6717   
1676         Elizabeth, NJ 07201                40.6717   
1678         Elizabeth, NJ 07201                40.6717   
1686         Elizabeth, NJ 07201                40.6717   
1695         Elizabeth, NJ 07201                40.6717   
1748           Garwood, NJ 07027                40.6512   
1778           Garwood, NJ 07027                40.6512   
1784           Garwood, NJ 07027                40.6512   
2052        Plainfield, NJ 07061                40.6657   
2056        Plainfield, NJ 07061                40.6657   
2173           Fanwood, NJ 07023                40.6419   
2177           Fanwood, NJ 07023                40.6419   
2193           Fanwood, NJ 07023                40.6419   
2443    

Showing the result count by neighborhood. 

In [27]:
nj_venues.groupby('Neighborhood')['Venue'].count()

Neighborhood
Belleville, NJ 07109          100
Berkeley Heights, NJ 07922    100
Bloomfield, NJ 07003          100
Caldwell, NJ 07006            100
Caldwell, NJ 07007            100
Cedar Grove, NJ 07009         100
Clark, NJ 07066               100
Cranford, NJ 07016            100
East Orange, NJ 07017         100
East Orange, NJ 07018         100
East Orange, NJ 07019         100
Elizabeth, NJ 07201           100
Elizabeth, NJ 07202           100
Elizabeth, NJ 07207           100
Elizabeth, NJ 07208           100
Elizabethport, NJ 07206       100
Essex Fells, NJ 07021         100
Fairfield, NJ 07004           100
Fanwood, NJ 07023             100
Garwood, NJ 07027             100
Glen Ridge, NJ 07028          100
Hillside, NJ 07205            100
Irvington, NJ 07111           100
Kenilworth, NJ 07033          100
Linden, NJ 07036              100
Livingston, NJ 07039          100
Maplewood, NJ 07040           100
Millburn, NJ 07041            100
Montclair, NJ 07042           100
M

Listing unique categories returned. 

In [37]:
nj_venues['Venue Category'].unique()


array(['Grocery Store', 'Liquor Store', 'Pet Store', 'Big Box Store',
       'Pharmacy', 'Market', 'Convenience Store', 'Supermarket',
       'Warehouse Store', 'Hobby Shop', 'Video Game Store',
       'Cosmetics Shop', 'Furniture / Home Store', 'Dry Cleaner',
       'Discount Store', 'Electronics Store',
       'Paper / Office Supplies Store', 'Thrift / Vintage Store',
       'Shipping Store', 'Department Store', 'Business Service',
       'Construction & Landscaping', 'Other Repair Shop', 'Print Shop',
       'Shopping Mall', 'Lawyer', 'Massage Studio', 'Sporting Goods Shop',
       'Arts & Crafts Store', 'Mobile Phone Shop', 'ATM', 'Flower Shop',
       'Gift Shop', 'Gourmet Shop', 'Toy / Game Store', 'Kids Store',
       'Wine Shop', 'Home Service', 'Locksmith', 'Optical Shop',
       'Kitchen Supply Store', 'Farmers Market', 'Cheese Shop',
       'Record Shop', "Women's Store", 'Bookstore', 'Smoothie Shop',
       'Lingerie Store', 'Chocolate Shop', 'Clothing Store',
       'Music

Listing venue counts by category and neighborhood using onehot encoding. 

In [38]:
# one hot encoding
nj_onehot = pd.get_dummies(nj_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nj_onehot['Neighborhood'] = nj_venues['Neighborhood'] 

nj_onehot['Neighborhood']
nj_onehot.head()

# move neighborhood column to the first column

col_name='Neighborhood'
neighborhood_col = nj_onehot.pop(col_name)
nj_onehot.insert(0, col_name, neighborhood_col)
nj_onehot.head()


Neighborhood  ATM  Accessories Store  Antique Shop  \
0  Vauxhall, NJ 07088    0                  0             0   
1  Vauxhall, NJ 07088    0                  0             0   
2  Vauxhall, NJ 07088    0                  0             0   
3  Vauxhall, NJ 07088    0                  0             0   
4  Vauxhall, NJ 07088    0                  0             0   

   Arts & Crafts Store  Astrologer  Auto Garage  Auto Workshop  Baby Store  \
0                    0           0            0              0           0   
1                    0           0            0              0           0   
2                    0           0            0              0           0   
3                    0           0            0              0           0   
4                    0           0            0              0           0   

   Beer Store  Big Box Store  Board Shop  Bookstore  Boutique  Bridal Shop  \
0           0              0           0          0         0            0   
1           0              0           0          0         0            0   
2           0              0           0          0         0            0   
3           0              0           0          0         0            0   
4           0              1           0          0         0            0   

   Business Service  Candy Store  Carpet Store  Check Cashing Service  \
0                 0            0             0                      0   
1                 0            0             0                      0   
2                 0            0             0                      0   
3                 0            0             0                      0   
4                 0            0             0                      0   

   Cheese Shop  Child Care Service  Chocolate Shop  Clothing Store  \
0            0                   0               0               0   
1            0                   0               0               0   
2            0                   0               0               0   
3            0                   0               0               0   
4            0                   0               0               0   

   Comic Shop  Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0           0                           0                  0               0   
1           0                           0                  0               0   
2           0                           0                  0               0   
3           0                           0                  0               0   
4           0                           0                  0               0   

   Costume Shop  Currency Exchange  Department Store  Discount Store  \
0             0                  0                 0               0   
1             0                  0                 0               0   
2             0                  0                 0               0   
3             0                  0                 0               0   
4             0                  0                 0               0   

   Drugstore  Dry Cleaner  Electronics Store  Event Service  Fabric Shop  \
0          0            0                  0              0            0   
1          0            0                  0              0            0   
2          0            0                  0              0            0   
3          0            0                  0              0            0   
4          0            0                  0              0            0   

   Farmers Market  Film Studio  Fish Market  Fishing Store  Flea Market  \
0               0            0            0              0            0   
1               0            0            0              0            0   
2               0            0            0              0            0   
3               0            0            0              0            0   
4               0            0            0              0            0   

   Flower 

Listing frequency account of venues by neighborhood. 

In [40]:

nj_grouped = nj_onehot.groupby('Neighborhood').mean().reset_index()
nj_grouped

Neighborhood   ATM  Accessories Store  Antique Shop  \
0         Belleville, NJ 07109  0.01               0.00          0.00   
1   Berkeley Heights, NJ 07922  0.00               0.00          0.00   
2         Bloomfield, NJ 07003  0.01               0.00          0.01   
3           Caldwell, NJ 07006  0.01               0.01          0.00   
4           Caldwell, NJ 07007  0.01               0.01          0.00   
5        Cedar Grove, NJ 07009  0.01               0.01          0.00   
6              Clark, NJ 07066  0.01               0.00          0.00   
7           Cranford, NJ 07016  0.00               0.00          0.00   
8        East Orange, NJ 07017  0.01               0.00          0.00   
9        East Orange, NJ 07018  0.01               0.00          0.00   
10       East Orange, NJ 07019  0.02               0.00          0.00   
11         Elizabeth, NJ 07201  0.00               0.02          0.00   
12         Elizabeth, NJ 07202  0.01               0.00          0.00   
13         Elizabeth, NJ 07207  0.00               0.02          0.00   
14         Elizabeth, NJ 07208  0.02               0.00          0.00   
15     Elizabethport, NJ 07206  0.00               0.02          0.00   
16       Essex Fells, NJ 07021  0.01               0.00          0.00   
17         Fairfield, NJ 07004  0.00               0.00          0.00   
18           Fanwood, NJ 07023  0.00               0.01          0.00   
19           Garwood, NJ 07027  0.01               0.01          0.00   
20        Glen Ridge, NJ 07028  0.00               0.00          0.02   
21          Hillside, NJ 07205  0.02               0.00          0.00   
22         Irvington, NJ 07111  0.01               0.00          0.00   
23        Kenilworth, NJ 07033  0.00               0.00          0.00   
24            Linden, NJ 07036  0.01               0.01          0.00   
25        Livingston, NJ 07039  0.00               0.02          0.00   
26         Maplewood, NJ 07040  0.00               0.00          0.00   
27          Millburn, NJ 07041  0.01               0.00          0.00   
28         Montclair, NJ 07042  0.00               0.01          0.02   
29         Montclair, NJ 07043  0.01               0.01          0.00   
30      Mountainside, NJ 07092  0.00               0.02          0.00   
31    New Providence, NJ 07974  0.00               0.00          0.00   
32            Newark, NJ 07101  0.02               0.00          0.00   
33            Newark, NJ 07102  0.00               0.00          0.00   
34            Newark, NJ 07103  0.02               0.01          0.00   
35            Newark, NJ 07104  0.01               0.00          0.00   
36            Newark, NJ 07105  0.01               0.01          0.00   
37            Newark, NJ 07106  0.02               0.00          0.00   
38            Newark, NJ 07107  0.01               0.00          0.00   
39            Newark, NJ 07108  0.01               0.00          0.00   
40            Newark, NJ 07112  0.00               0.01          0.00   
41            Newark, NJ 07114  0.00               0.01          0.00   
42            Newark, NJ 07175  0.00               0.01          0.00   
43            Newark, NJ 07184  0.00               0.00          0.00   
44            Newark, NJ 07188  0.00               0.01          0.00   
45            Newark, NJ 07189  0.00               0.00          0.00   
46            Newark, NJ 07191  0.00               0.00          0.00   
47            Newark, NJ 07192  0.00               0.01          0.00   
48            Newark, NJ 07193  0.00               0.01          0.00   
49            Newark, NJ 07195  0.00               0.01          0.00   
50            Newark, NJ 07198  0.00               0.00          0.00   
51            Newark, NJ 07199  0.00               0.01          0.00   
52            Nutley, NJ 07110  0.00               0.00          0.00   
53            Orange, NJ 07050  0.00               0.00          0.00   
54 

In [44]:
nj_grouped[['Neighborhood', 'Lawyer']].sort_values('Lawyer', ascending=False)

Neighborhood  Lawyer
42            Newark, NJ 07175    0.12
44            Newark, NJ 07188    0.12
47            Newark, NJ 07192    0.12
48            Newark, NJ 07193    0.12
49            Newark, NJ 07195    0.12
51            Newark, NJ 07199    0.12
14         Elizabeth, NJ 07208    0.11
60          Roseland, NJ 07068    0.11
12         Elizabeth, NJ 07202    0.10
33            Newark, NJ 07102    0.09
11         Elizabeth, NJ 07201    0.08
13         Elizabeth, NJ 07207    0.08
2         Bloomfield, NJ 07003    0.06
36            Newark, NJ 07105    0.06
6              Clark, NJ 07066    0.06
4           Caldwell, NJ 07007    0.06
72       West Orange, NJ 07052    0.06
46            Newark, NJ 07191    0.05
54            Orange, NJ 07051    0.05
43            Newark, NJ 07184    0.05
45            Newark, NJ 07189    0.05
70          Vauxhall, NJ 07088    0.05
50            Newark, NJ 07198    0.05
71            Verona, NJ 07044    0.04
73         Westfield, NJ 07090    0.04
28         Montclair, NJ 07042    0.04
53            Orange, NJ 07050    0.04
52            Nutley, NJ 07110    0.04
16       Essex Fells, NJ 07021    0.04
26         Maplewood, NJ 07040    0.03
41            Newark, NJ 07114    0.03
19           Garwood, NJ 07027    0.03
18           Fanwood, NJ 07023    0.03
65      South Orange, NJ 07079    0.03
7           Cranford, NJ 07016    0.03
55        Plainfield, NJ 07060    0.02
56        Plainfield, NJ 07061    0.02
67            Summit, NJ 07901    0.02
68            Summit, NJ 07902    0.02
37            Newark, NJ 07106    0.02
74         Westfield, NJ 07091    0.02
39            Newark, NJ 07108    0.02
9        East Orange, NJ 07018    0.02
31    New Providence, NJ 07974    0.02
30      Mountainside, NJ 07092    0.02
29         Montclair, NJ 07043    0.02
58        Plainfield, NJ 07063    0.01
3           Caldwell, NJ 07006    0.01
8        East Orange, NJ 07017    0.01
69             Union, NJ 07083    0.01
10       East Orange, NJ 07019    0.01
17         Fairfield, NJ 07004    0.01
64       Short Hills, NJ 07078    0.01
62           Roselle, NJ 07203    0.01
20        Glen Ridge, NJ 07028    0.01
0         Belleville, NJ 07109    0.01
27          Millburn, NJ 07041    0.01
38            Newark, NJ 07107    0.01
1   Berkeley Heights, NJ 07922    0.01
35            Newark, NJ 07104    0.01
24            Linden, NJ 07036    0.01
34            Newark, NJ 07103    0.01
66       Springfield, NJ 07081    0.00
5        Cedar Grove, NJ 07009    0.00
32            Newark, NJ 07101    0.00
15     Elizabethport, NJ 07206    0.00
21          Hillside, NJ 07205    0.00
57        Plainfield, NJ 07062    0.00
25        Livingston, NJ 07039    0.00
63     Scotch Plains, NJ 07076    0.00
61      Roselle Park, NJ 07204    0.00
23        Kenilworth, NJ 07033    0.00
59            Rahway, NJ 07065    0.00
22         Irvington, NJ 07111    0.00
40            Newark, NJ 07112    0.00

Analyze neighborhoods by the most common venues. 

In [45]:

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = nj_grouped['Neighborhood']

for ind in np.arange(nj_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(nj_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted

Neighborhood       1st Most Common Venue  \
0         Belleville, NJ 07109                    Pharmacy   
1   Berkeley Heights, NJ 07922                    Pharmacy   
2         Bloomfield, NJ 07003                Liquor Store   
3           Caldwell, NJ 07006                    Pharmacy   
4           Caldwell, NJ 07007                    Pharmacy   
5        Cedar Grove, NJ 07009      Furniture / Home Store   
6              Clark, NJ 07066                    Pharmacy   
7           Cranford, NJ 07016           Convenience Store   
8        East Orange, NJ 07017                    Pharmacy   
9        East Orange, NJ 07018                Liquor Store   
10       East Orange, NJ 07019                    Pharmacy   
11         Elizabeth, NJ 07201              Clothing Store   
12         Elizabeth, NJ 07202                      Lawyer   
13         Elizabeth, NJ 07207              Clothing Store   
14         Elizabeth, NJ 07208                    Pharmacy   
15     Elizabethport, NJ 07206              Clothing Store   
16       Essex Fells, NJ 07021                    Pharmacy   
17         Fairfield, NJ 07004                Home Service   
18           Fanwood, NJ 07023  Construction & Landscaping   
19           Garwood, NJ 07027                    Pharmacy   
20        Glen Ridge, NJ 07028                Liquor Store   
21          Hillside, NJ 07205           Convenience Store   
22         Irvington, NJ 07111                Liquor Store   
23        Kenilworth, NJ 07033                    Pharmacy   
24            Linden, NJ 07036                    Pharmacy   
25        Livingston, NJ 07039                    Pharmacy   
26         Maplewood, NJ 07040                Liquor Store   
27          Millburn, NJ 07041                    Pharmacy   
28         Montclair, NJ 07042                    Pharmacy   
29         Montclair, NJ 07043                    Pharmacy   
30      Mountainside, NJ 07092                    Pharmacy   
31    New Providence, NJ 07974                Liquor Store   
32            Newark, NJ 07101                Liquor Store   
33            Newark, NJ 07102                      Lawyer   
34            Newark, NJ 07103                Liquor Store   
35            Newark, NJ 07104                Liquor Store   
36            Newark, NJ 07105           Convenience Store   
37            Newark, NJ 07106                Liquor Store   
38            Newark, NJ 07107                Liquor Store   
39            Newark, NJ 07108                Liquor Store   
40            Newark, NJ 07112                Liquor Store   
41            Newark, NJ 07114                Liquor Store   
42            Newark, NJ 07175                      Lawyer   
43            Newark, NJ 07184                    Pharmacy   
44            Newark, NJ 07188                      Lawyer   
45            Newark, NJ 07189                    Pharmacy   
46            Newark, NJ 07191                    Pharmacy   
47            Newark, NJ 07192                      Lawyer   
48            Newark, NJ 07193                      Lawyer   
49            Newark, NJ 07195                      Lawyer   
50            Newark, NJ 07198                    Pharmacy   
51            Newark, NJ 07199                      Lawyer   
52            Nutley, NJ 07110                    Pharmacy   
53            Orange, NJ 07050                    Pharmacy   
54            Orange, NJ 07051                    Pharmacy   
55        Plainfield, NJ 07060           Convenience Store   
56        Plainfield, NJ 07061                Home Service   
57        Plainfield, NJ 07062                Liquor Store   
58        Plainfield, NJ 07063           Convenience Store   
59            Rahway, NJ 07065           Convenience Store   
60          Roseland, NJ 07068                    Pharmacy   
61      Roselle Park, NJ 07204                    Pharmacy   
62           Roselle, NJ 07203                    Pharmacy   
63     Scotch Plains, NJ 07076                    

Next steps will be using k-means clustering to identify similar neighborhoods, then identify the cluster with the highest frequency of lawyer venues.  Ideal locations will be neighborhoods in that cluster that themselves have a low frequency of lawyer venues.  